### Lab 12
#### tenserflow에서 cell 생성 필요
#### hidden size, sequence_length, shape에 주면 알아서 dynamic하게 설정

In [7]:
import tensorflow as tf
import numpy as np
tf.set_random_seed(777)

idx2char = ['h', 'i', 'e', 'l', 'o']
# 각각 one hot으로 치환
x_data = [[0, 1, 0, 2, 3, 3]]   # hihell
x_one_hot = [[[1, 0, 0, 0, 0],   # h 0
              [0, 1, 0, 0, 0],   # i 1
              [1, 0, 0, 0, 0],   # h 0
              [0, 0, 1, 0, 0],   # e 2
              [0, 0, 0, 1, 0],   # l 3
              [0, 0, 0, 1, 0]]]  # l 3

y_data = [[1, 0, 2, 3, 3, 4]]    # ihello

num_classes = 5
input_dim = 5  # one hot 사이즈
hidden_size = 5  #  Lstm
batch_size = 1
sequence_length = 6  # ihello 길이
learning_rate = 0.1

X = tf.placeholder(
    tf.float32, [None, sequence_length, input_dim])  # X one-hot
Y = tf.placeholder(tf.int32, [None, sequence_length])  # Y label

cell = tf.contrib.rnn.BasicLSTMCell(num_units=hidden_size, state_is_tuple=True)
initial_state = cell.zero_state(batch_size, tf.float32)
outputs, _states = tf.nn.dynamic_rnn(
    cell, X, initial_state=initial_state, dtype=tf.float32)

X_for_fc = tf.reshape(outputs, [-1, hidden_size])

outputs = tf.contrib.layers.fully_connected(
    inputs=X_for_fc, num_outputs=num_classes, activation_fn=None)

outputs = tf.reshape(outputs, [batch_size, sequence_length, num_classes])

weights = tf.ones([batch_size, sequence_length])
sequence_loss = tf.contrib.seq2seq.sequence_loss(
    logits=outputs, targets=Y, weights=weights)
loss = tf.reduce_mean(sequence_loss)
train = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(loss)

prediction = tf.argmax(outputs, axis=2)

with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    for i in range(50):
        l, _ = sess.run([loss, train], feed_dict={X: x_one_hot, Y: y_data})
        result = sess.run(prediction, feed_dict={X: x_one_hot})
        print(i, "loss:", l, "prediction: ", result, "true Y: ", y_data)

        result_str = [idx2char[c] for c in np.squeeze(result)]
        print("\tPrediction str: ", ''.join(result_str))

ValueError: Variable rnn/basic_lstm_cell/kernel already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 1768, in __init__
    self._traceback = tf_stack.extract_stack()
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 3272, in create_op
    op_def=op_def)
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\util\deprecation.py", line 488, in new_func
    return func(*args, **kwargs)


In [8]:
import tensorflow as tf
import numpy as np
tf.set_random_seed(777)

sample = " if you want you"
idx2char = list(set(sample))  # index -> char
char2idx = {c: i for i, c in enumerate(idx2char)}  # char -> index

dic_size = len(char2idx)  # RNN input size
hidden_size = len(char2idx)  # RNN output size
num_classes = len(char2idx)  # final output size
batch_size = 1
sequence_length = len(sample) - 1
learning_rate = 0.1

sample_idx = [char2idx[c] for c in sample]
x_data = [sample_idx[:-1]]  # X data sample (0 ~ n-1) hello: hell
y_data = [sample_idx[1:]]   # Y label sample (1 ~ n) hello: ello

X = tf.placeholder(tf.int32, [None, sequence_length])
Y = tf.placeholder(tf.int32, [None, sequence_length])

x_one_hot = tf.one_hot(X, num_classes)  # one hot
cell = tf.contrib.rnn.BasicLSTMCell(
    num_units=hidden_size, state_is_tuple=True)
initial_state = cell.zero_state(batch_size, tf.float32)
outputs, _states = tf.nn.dynamic_rnn(
    cell, x_one_hot, initial_state=initial_state, dtype=tf.float32)


X_for_fc = tf.reshape(outputs, [-1, hidden_size])
outputs = tf.contrib.layers.fully_connected(X_for_fc, num_classes, activation_fn=None)


outputs = tf.reshape(outputs, [batch_size, sequence_length, num_classes])

weights = tf.ones([batch_size, sequence_length])
sequence_loss = tf.contrib.seq2seq.sequence_loss(
    logits=outputs, targets=Y, weights=weights)
loss = tf.reduce_mean(sequence_loss)
#gradient x adam 사용
train = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(loss)

prediction = tf.argmax(outputs, axis=2)

with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    for i in range(3000):
        l, _ = sess.run([loss, train], feed_dict={X: x_data, Y: y_data})
        result = sess.run(prediction, feed_dict={X: x_data})

        result_str = [idx2char[c] for c in np.squeeze(result)]

        print(i, "loss:", l, "Prediction:", ''.join(result_str))

ValueError: Variable rnn/basic_lstm_cell/kernel already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 1768, in __init__
    self._traceback = tf_stack.extract_stack()
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 3272, in create_op
    op_def=op_def)
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\util\deprecation.py", line 488, in new_func
    return func(*args, **kwargs)


In [5]:
from __future__ import print_function

import tensorflow as tf
import numpy as np
from tensorflow.contrib import rnn

tf.set_random_seed(777)  # reproducibility

sentence = ("if you want to build a ship, don't drum up people together to "
            "collect wood and don't assign them tasks and work, but rather "
            "teach them to long for the endless immensity of the sea.")

char_set = list(set(sentence))
char_dic = {w: i for i, w in enumerate(char_set)}

data_dim = len(char_set)
hidden_size = len(char_set)
num_classes = len(char_set)
sequence_length = 10  # Any arbitrary number
learning_rate = 0.1

dataX = []
dataY = []
for i in range(0, len(sentence) - sequence_length):
    x_str = sentence[i:i + sequence_length]
    y_str = sentence[i + 1: i + sequence_length + 1]
    print(i, x_str, '->', y_str)

    x = [char_dic[c] for c in x_str]  # x str to index
    y = [char_dic[c] for c in y_str]  # y str to index

    dataX.append(x)
    dataY.append(y)

batch_size = len(dataX)

X = tf.placeholder(tf.int32, [None, sequence_length])
Y = tf.placeholder(tf.int32, [None, sequence_length])

# One-hot encoding
X_one_hot = tf.one_hot(X, num_classes)
print(X_one_hot)  # check out the shape


# Make a lstm cell with hidden_size (each unit output vector size)
def lstm_cell():
    cell = rnn.BasicLSTMCell(hidden_size, state_is_tuple=True)
    return cell

multi_cells = rnn.MultiRNNCell([lstm_cell() for _ in range(2)], state_is_tuple=True)

# outputs: unfolding size x hidden size, state = hidden size
outputs, _states = tf.nn.dynamic_rnn(multi_cells, X_one_hot, dtype=tf.float32)

# FC layer
X_for_fc = tf.reshape(outputs, [-1, hidden_size])
outputs = tf.contrib.layers.fully_connected(X_for_fc, num_classes, activation_fn=None)

# reshape out for sequence_loss
outputs = tf.reshape(outputs, [batch_size, sequence_length, num_classes])

# All weights are 1 (equal weights)
weights = tf.ones([batch_size, sequence_length])

sequence_loss = tf.contrib.seq2seq.sequence_loss(
    logits=outputs, targets=Y, weights=weights)
mean_loss = tf.reduce_mean(sequence_loss)
train_op = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(mean_loss)

sess = tf.Session()
sess.run(tf.global_variables_initializer())

for i in range(500):
    _, l, results = sess.run(
        [train_op, mean_loss, outputs], feed_dict={X: dataX, Y: dataY})
    for j, result in enumerate(results):
        index = np.argmax(result, axis=1)
        print(i, j, ''.join([char_set[t] for t in index]), l)

# Let's print the last char of each result to check it works
results = sess.run(outputs, feed_dict={X: dataX})
for j, result in enumerate(results):
    index = np.argmax(result, axis=1)
    if j is 0:  # print all for the first result to make a sentence
        print(''.join([char_set[t] for t in index]), end='')
    else:
        print(char_set[index[-1]], end='')

0 if you wan -> f you want
1 f you want ->  you want 
2  you want  -> you want t
3 you want t -> ou want to
4 ou want to -> u want to 
5 u want to  ->  want to b
6  want to b -> want to bu
7 want to bu -> ant to bui
8 ant to bui -> nt to buil
9 nt to buil -> t to build
10 t to build ->  to build 
11  to build  -> to build a
12 to build a -> o build a 
13 o build a  ->  build a s
14  build a s -> build a sh
15 build a sh -> uild a shi
16 uild a shi -> ild a ship
17 ild a ship -> ld a ship,
18 ld a ship, -> d a ship, 
19 d a ship,  ->  a ship, d
20  a ship, d -> a ship, do
21 a ship, do ->  ship, don
22  ship, don -> ship, don'
23 ship, don' -> hip, don't
24 hip, don't -> ip, don't 
25 ip, don't  -> p, don't d
26 p, don't d -> , don't dr
27 , don't dr ->  don't dru
28  don't dru -> don't drum
29 don't drum -> on't drum 
30 on't drum  -> n't drum u
31 n't drum u -> 't drum up
32 't drum up -> t drum up 
33 t drum up  ->  drum up p
34  drum up p -> drum up pe
35 drum up pe -> rum up peo
36

1 160 ssssssssss 3.07447
1 161 ssssssssss 3.07447
1 162 ssssssssss 3.07447
1 163   ssssssss 3.07447
1 164  sssssssss 3.07447
1 165  hssssssss 3.07447
1 166  sssssssss 3.07447
1 167 ssssssssss 3.07447
1 168 ssssssssss 3.07447
1 169   ssssssss 3.07447
2 0            3.0414386
2 1  t         3.0414386
2 2 tt         3.0414386
2 3            3.0414386
2 4            3.0414386
2 5  tt        3.0414386
2 6 ttt        3.0414386
2 7 tt         3.0414386
2 8            3.0414386
2 9            3.0414386
2 10            3.0414386
2 11 tt         3.0414386
2 12            3.0414386
2 13  t         3.0414386
2 14 tt         3.0414386
2 15            3.0414386
2 16            3.0414386
2 17            3.0414386
2 18            3.0414386
2 19            3.0414386
2 20 tt         3.0414386
2 21            3.0414386
2 22 tt         3.0414386
2 23            3.0414386
2 24            3.0414386
2 25  tt        3.0414386
2 26 ttt        3.0414386
2 27  t         3.0414386
2 28 tt         3.0414386
2 29  

4 24            2.8631074
4 25  o oo      2.8631074
4 26 oooo       2.8631074
4 27            2.8631074
4 28 oo         2.8631074
4 29            2.8631074
4 30            2.8631074
4 31            2.8631074
4 32            2.8631074
4 33          o 2.8631074
4 34 oo  oooooo 2.8631074
4 35     oooooo 2.8631074
4 36    ooooooo 2.8631074
4 37 oooooooooo 2.8631074
4 38 oooooooooo 2.8631074
4 39 oooooooooo 2.8631074
4 40 oooooooooo 2.8631074
4 41 oooooooooo 2.8631074
4 42 oooooooooo 2.8631074
4 43 oooooooo   2.8631074
4 44            2.8631074
4 45     o      2.8631074
4 46 ooooo      2.8631074
4 47   o        2.8631074
4 48  o         2.8631074
4 49 oo         2.8631074
4 50            2.8631074
4 51            2.8631074
4 52            2.8631074
4 53            2.8631074
4 54            2.8631074
4 55            2.8631074
4 56            2.8631074
4 57            2.8631074
4 58 oo         2.8631074
4 59            2.8631074
4 60            2.8631074
4 61 ooo        2.8631074
4 62 o      

6 0            2.8018072
6 1            2.8018072
6 2            2.8018072
6 3            2.8018072
6 4            2.8018072
6 5   o        2.8018072
6 6  o         2.8018072
6 7 o          2.8018072
6 8            2.8018072
6 9            2.8018072
6 10            2.8018072
6 11            2.8018072
6 12            2.8018072
6 13            2.8018072
6 14            2.8018072
6 15            2.8018072
6 16            2.8018072
6 17            2.8018072
6 18            2.8018072
6 19            2.8018072
6 20            2.8018072
6 21            2.8018072
6 22            2.8018072
6 23            2.8018072
6 24            2.8018072
6 25            2.8018072
6 26 o          2.8018072
6 27            2.8018072
6 28            2.8018072
6 29            2.8018072
6 30            2.8018072
6 31            2.8018072
6 32            2.8018072
6 33            2.8018072
6 34         oo 2.8018072
6 35        ooo 2.8018072
6 36       oooo 2.8018072
6 37    ooooooo 2.8018072
6 38    oooooo  2.8018

8 94   ooo      2.6947856
8 95  oo      t 2.6947856
8 96 o      nt  2.6947856
8 97       nt n 2.6947856
8 98      n  nn 2.6947856
8 99        nnn 2.6947856
8 100       nnn  2.6947856
8 101        n   2.6947856
8 102 o    on    2.6947856
8 103      n     2.6947856
8 104    on      2.6947856
8 105   on     n 2.6947856
8 106 ooo   oooo 2.6947856
8 107 o     oooo 2.6947856
8 108      ooooo 2.6947856
8 109     oooooo 2.6947856
8 110     nnooo  2.6947856
8 111    o oo    2.6947856
8 112 o o oo     2.6947856
8 113            2.6947856
8 114          o 2.6947856
8 115         oo 2.6947856
8 116 o      oo  2.6947856
8 117       ooo  2.6947856
8 118       oo   2.6947856
8 119     ooo    2.6947856
8 120    ooo   o 2.6947856
8 121         o  2.6947856
8 122        o   2.6947856
8 123 o     oo   2.6947856
8 124      oo  o 2.6947856
8 125     oo  oo 2.6947856
8 126        ooo 2.6947856
8 127   o   oooo 2.6947856
8 128      ooooo 2.6947856
8 129 o   oooooo 2.6947856
8 130     oooooo 2.6947856
8 131  

...

492 32 t drum up  0.22962637
492 33  drum up p 0.22962637
492 34 toum up pe 0.22962637
492 35  um up peo 0.22962637
492 36  m up peop 0.22962637
492 37 m up peopl 0.22962637
492 38  tp people 0.22962637
492 39 tp people  0.22962637
492 40 m people t 0.22962637
492 41 lpeople to 0.22962637
492 42 teople tog 0.22962637
492 43 lople toge 0.22962637
492 44 nple toget 0.22962637
492 45 nle togeth 0.22962637
492 46 le togethe 0.22962637
492 47 ectogether 0.22962637
492 48 neogether  0.22962637
492 49 to ether t 0.22962637
492 50   ether to 0.22962637
492 51 nether to  0.22962637
492 52 nther to c 0.22962637
492 53 nher to co 0.22962637
492 54  em to col 0.22962637
492 55 er to coll 0.22962637
492 56 n to colle 0.22962637
492 57  to collec 0.22962637
492 58 to lollect 0.22962637
492 59   lollect  0.22962637
492 60 nbollect w 0.22962637
492 61 tollect wo 0.22962637
492 62 ollect woo 0.22962637
492 63 nlect wood 0.22962637
492 64 eect wood  0.22962637
492 65 ect wood a 0.22962637
492 66 nt wood

494 0 l you want 0.22954832
494 1 oyou want  0.22954832
494 2 tou want t 0.22954832
494 3 ou want to 0.22954832
494 4 n want to  0.22954832
494 5 pwant to b 0.22954832
494 6 tont to bu 0.22954832
494 7 ont to bui 0.22954832
494 8 nd to buil 0.22954832
494 9 d to build 0.22954832
494 10  do build  0.22954832
494 11 to build a 0.22954832
494 12   build a  0.22954832
494 13 nluild a s 0.22954832
494 14 tutld a sh 0.22954832
494 15 uild a shi 0.22954832
494 16 pld a ship 0.22954832
494 17 ld a ship, 0.22954832
494 18 e a ship,  0.22954832
494 19  anship, d 0.22954832
494 20 tnship, do 0.22954832
494 21 nship, don 0.22954832
494 22 thip, don' 0.22954832
494 23 sip, don't 0.22954832
494 24 ep, don't  0.22954832
494 25 l, don't d 0.22954832
494 26 l don't dr 0.22954832
494 27  bon't dru 0.22954832
494 28 ton't arum 0.22954832
494 29  n't arum  0.22954832
494 30 n't arum u 0.22954832
494 31 dt arum up 0.22954832
494 32 t arum up  0.22954832
494 33  drum up p 0.22954832
494 34 toum up pe 0.2295

496 0 l you want 0.22931089
496 1 oyou want  0.22931089
496 2 tou want t 0.22931089
496 3 ou want to 0.22931089
496 4 n want to  0.22931089
496 5 pwant to b 0.22931089
496 6 tont to bu 0.22931089
496 7 ont to bui 0.22931089
496 8 nd to buil 0.22931089
496 9 d to build 0.22931089
496 10  ao build  0.22931089
496 11 to build a 0.22931089
496 12   build a  0.22931089
496 13 nluild a s 0.22931089
496 14 tutld a sh 0.22931089
496 15 utld a shi 0.22931089
496 16 pld a ship 0.22931089
496 17 ld a ship, 0.22931089
496 18 e a ship,  0.22931089
496 19  a ship, d 0.22931089
496 20 tnship, do 0.22931089
496 21 nship, don 0.22931089
496 22 thip, don' 0.22931089
496 23 sip, don't 0.22931089
496 24 ep, don't  0.22931089
496 25 l, don't d 0.22931089
496 26 l don't dr 0.22931089
496 27  bon't dru 0.22931089
496 28 ton't arum 0.22931089
496 29  n't arum  0.22931089
496 30 n't arum u 0.22931089
496 31 dt arum up 0.22931089
496 32 t arum up  0.22931089
496 33  arum up p 0.22931089
496 34 toum up pe 0.2293

497 155 ns immensi 0.22920796
497 156 iiimmensit 0.22920796
497 157 iimmensity 0.22920796
497 158 tmmensity  0.22920796
497 159 mmensity o 0.22920796
497 160  ensity of 0.22920796
497 161  nsity of  0.22920796
497 162 ndity of t 0.22920796
497 163 dity of th 0.22920796
497 164 igy of the 0.22920796
497 165 my of the  0.22920796
497 166   of the s 0.22920796
497 167  of the se 0.22920796
497 168 tf the sea 0.22920796
497 169 n the sea. 0.22920796
498 0 p you want 0.22910549
498 1 oyou want  0.22910549
498 2 tou want t 0.22910549
498 3 ou want to 0.22910549
498 4   want to  0.22910549
498 5 twant to b 0.22910549
498 6 tont to bu 0.22910549
498 7 ont to bui 0.22910549
498 8 sd to buil 0.22910549
498 9 d to build 0.22910549
498 10 hto build  0.22910549
498 11 to luild a 0.22910549
498 12 h luild a  0.22910549
498 13  luild a s 0.22910549
498 14 tutld a sh 0.22910549
498 15 utld a shi 0.22910549
498 16 tld a ship 0.22910549
498 17 pd a ship, 0.22910549
498 18 e a ship,  0.22910549
498 19  a

m you want to build a ship, don't drum up people together to collect wood and don't assign them tasks and work, but rather teach them to long for the endless immensity of the sea.

In [6]:
import tensorflow as tf
import numpy as np
import matplotlib
import os

tf.set_random_seed(777)  # reproducibility

if "DISPLAY" not in os.environ:
    # remove Travis CI Error
    matplotlib.use('Agg')

import matplotlib.pyplot as plt


def MinMaxScaler(data):

    numerator = data - np.min(data, 0)
    denominator = np.max(data, 0) - np.min(data, 0)

    return numerator / (denominator + 1e-7)



seq_length = 7
data_dim = 5
hidden_dim = 10
output_dim = 1
learning_rate = 0.01
iterations = 500


xy = np.loadtxt('data-02-stock_daily.csv', delimiter=',')
xy = xy[::-1]


train_size = int(len(xy) * 0.7)
train_set = xy[0:train_size]
test_set = xy[train_size - seq_length:]

train_set = MinMaxScaler(train_set)
test_set = MinMaxScaler(test_set)

def build_dataset(time_series, seq_length):
    dataX = []
    dataY = []
    for i in range(0, len(time_series) - seq_length):
        _x = time_series[i:i + seq_length, :]
        _y = time_series[i + seq_length, [-1]]
        print(_x, "->", _y)
        dataX.append(_x)
        dataY.append(_y)
    return np.array(dataX), np.array(dataY)

trainX, trainY = build_dataset(train_set, seq_length)
testX, testY = build_dataset(test_set, seq_length)

X = tf.placeholder(tf.float32, [None, seq_length, data_dim])
Y = tf.placeholder(tf.float32, [None, 1])

cell = tf.contrib.rnn.BasicLSTMCell(
    num_units=hidden_dim, state_is_tuple=True, activation=tf.tanh)
outputs, _states = tf.nn.dynamic_rnn(cell, X, dtype=tf.float32)
Y_pred = tf.contrib.layers.fully_connected(
    outputs[:, -1], output_dim, activation_fn=None)

loss = tf.reduce_sum(tf.square(Y_pred - Y))

optimizer = tf.train.AdamOptimizer(learning_rate)
train = optimizer.minimize(loss)

targets = tf.placeholder(tf.float32, [None, 1])
predictions = tf.placeholder(tf.float32, [None, 1])
rmse = tf.sqrt(tf.reduce_mean(tf.square(targets - predictions)))

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)

    for i in range(iterations):
        _, step_loss = sess.run([train, loss], feed_dict={
                                X: trainX, Y: trainY})
        print("[step: {}] loss: {}".format(i, step_loss))

    test_predict = sess.run(Y_pred, feed_dict={X: testX})
    rmse_val = sess.run(rmse, feed_dict={
                    targets: testY, predictions: test_predict})
    print("RMSE: {}".format(rmse_val))

    plt.plot(testY)
    plt.plot(test_predict)
    plt.xlabel("Time Period")
    plt.ylabel("Stock Price")
    plt.show()

[[2.53065030e-01 2.45070970e-01 2.33983036e-01 4.66075110e-04
  2.32039560e-01]
 [2.29604366e-01 2.39728936e-01 2.54567513e-01 2.98467330e-03
  2.37426028e-01]
 [2.49235510e-01 2.41668371e-01 2.48338489e-01 2.59926504e-04
  2.26793794e-01]
 [2.21013495e-01 2.46602231e-01 2.54710584e-01 0.00000000e+00
  2.62668239e-01]
 [3.63433786e-01 3.70389871e-01 2.67168847e-01 1.24764722e-02
  2.62105010e-01]
 [2.59447633e-01 3.10673724e-01 2.74113889e-01 4.56323384e-01
  2.71751265e-01]
 [2.76008150e-01 2.78314566e-01 1.98470380e-01 5.70171193e-01
  1.78104644e-01]] -> [0.16053716]
[[2.29604366e-01 2.39728936e-01 2.54567513e-01 2.98467330e-03
  2.37426028e-01]
 [2.49235510e-01 2.41668371e-01 2.48338489e-01 2.59926504e-04
  2.26793794e-01]
 [2.21013495e-01 2.46602231e-01 2.54710584e-01 0.00000000e+00
  2.62668239e-01]
 [3.63433786e-01 3.70389871e-01 2.67168847e-01 1.24764722e-02
  2.62105010e-01]
 [2.59447633e-01 3.10673724e-01 2.74113889e-01 4.56323384e-01
  2.71751265e-01]
 [2.76008150e-01 2.7831

 [0.29450074 0.31149027 0.32654153 0.1510173  0.32466509]] -> [0.34050775]
[[0.29964133 0.29781178 0.31997246 0.08688716 0.31878584]
 [0.29570834 0.29206137 0.31753804 0.10872995 0.31262499]
 [0.2979164  0.29148285 0.3110943  0.14284306 0.29245207]
 [0.27010846 0.26871923 0.28871977 0.14247558 0.28358042]
 [0.26948745 0.29100637 0.30465034 0.13197096 0.30769617]
 [0.29450074 0.31149027 0.32654153 0.1510173  0.32466509]
 [0.31861705 0.31836357 0.34882644 0.12876221 0.34050775]] -> [0.36448258]
[[0.29570834 0.29206137 0.31753804 0.10872995 0.31262499]
 [0.2979164  0.29148285 0.3110943  0.14284306 0.29245207]
 [0.27010846 0.26871923 0.28871977 0.14247558 0.28358042]
 [0.26948745 0.29100637 0.30465034 0.13197096 0.30769617]
 [0.29450074 0.31149027 0.32654153 0.1510173  0.32466509]
 [0.31861705 0.31836357 0.34882644 0.12876221 0.34050775]
 [0.33414248 0.34197789 0.36493623 0.33420274 0.36448258]] -> [0.33381857]
[[0.2979164  0.29148285 0.3110943  0.14284306 0.29245207]
 [0.27010846 0.268719

 [0.23715131 0.23808691 0.23497644 0.21422425 0.22115211]] -> [0.2152024]
[[0.10678059 0.13649309 0.13224183 0.14979833 0.15078511]
 [0.14787148 0.14772173 0.1650876  0.16463207 0.14582117]
 [0.13714161 0.15347214 0.15819624 0.14211706 0.16481462]
 [0.15991222 0.18709017 0.1885539  0.37437483 0.19169395]
 [0.24650991 0.25575524 0.24948395 0.44139105 0.25527513]
 [0.23715131 0.23808691 0.23497644 0.21422425 0.22115211]
 [0.20696305 0.20429899 0.22483108 0.13293    0.2152024 ]] -> [0.19900802]
[[0.14787148 0.14772173 0.1650876  0.16463207 0.14582117]
 [0.13714161 0.15347214 0.15819624 0.14211706 0.16481462]
 [0.15991222 0.18709017 0.1885539  0.37437483 0.19169395]
 [0.24650991 0.25575524 0.24948395 0.44139105 0.25527513]
 [0.23715131 0.23808691 0.23497644 0.21422425 0.22115211]
 [0.20696305 0.20429899 0.22483108 0.13293    0.2152024 ]
 [0.19257604 0.19633678 0.21244107 0.15155508 0.19900802]] -> [0.15767698]
[[0.13714161 0.15347214 0.15819624 0.14211706 0.16481462]
 [0.15991222 0.1870901

 [0.80334504 0.79628556 0.7658748  0.59567984 0.73736817]] -> [0.77531964]
[[0.58464397 0.57501353 0.6072855  0.14369454 0.59725092]
 [0.57453525 0.58130849 0.61580567 0.13170207 0.61098088]
 [0.58440244 0.57416288 0.56072895 0.2224702  0.55528621]
 [0.55028124 0.54404983 0.55190441 0.15982791 0.52828355]
 [0.52457805 0.55061685 0.56006668 0.36417496 0.56060203]
 [0.80334504 0.79628556 0.7658748  0.59567984 0.73736817]
 [0.71381524 0.75936729 0.76501566 0.24278032 0.77531964]] -> [0.76021641]
[[0.57453525 0.58130849 0.61580567 0.13170207 0.61098088]
 [0.58440244 0.57416288 0.56072895 0.2224702  0.55528621]
 [0.55028124 0.54404983 0.55190441 0.15982791 0.52828355]
 [0.52457805 0.55061685 0.56006668 0.36417496 0.56060203]
 [0.80334504 0.79628556 0.7658748  0.59567984 0.73736817]
 [0.71381524 0.75936729 0.76501566 0.24278032 0.77531964]
 [0.73392931 0.74055074 0.77679343 0.20058259 0.76021641]] -> [0.77591807]
[[0.58440244 0.57416288 0.56072895 0.2224702  0.55528621]
 [0.55028124 0.544049

 [0.62221547 0.65796926 0.6490556  0.27033253 0.67086521]] -> [0.66836577]
[[0.78716413 0.78607772 0.7671635  0.46256162 0.75852662]
 [0.72181947 0.70778356 0.68944413 0.45691494 0.67248474]
 [0.59754727 0.63986753 0.62826363 0.37998566 0.66956263]
 [0.61296926 0.69386699 0.64870491 0.32275701 0.65326254]
 [0.66313345 0.69866458 0.69653225 0.23573541 0.67442099]
 [0.62221547 0.65796926 0.6490556  0.27033253 0.67086521]
 [0.67486384 0.67294084 0.68389512 0.19122524 0.66836577]] -> [0.69864229]
[[0.72181947 0.70778356 0.68944413 0.45691494 0.67248474]
 [0.59754727 0.63986753 0.62826363 0.37998566 0.66956263]
 [0.61296926 0.69386699 0.64870491 0.32275701 0.65326254]
 [0.66313345 0.69866458 0.69653225 0.23573541 0.67442099]
 [0.62221547 0.65796926 0.6490556  0.27033253 0.67086521]
 [0.67486384 0.67294084 0.68389512 0.19122524 0.66836577]
 [0.68424797 0.68740194 0.70698548 0.22515909 0.69864229]] -> [0.75989968]
[[0.59754727 0.63986753 0.62826363 0.37998566 0.66956263]
 [0.61296926 0.693866

 [0.62634123 0.61385204 0.65731883 0.06377309 0.62015425]] -> [0.60557924]
[[0.65523643 0.64061289 0.66736934 0.08237202 0.65037944]
 [0.63737191 0.63961093 0.6678907  0.06302764 0.6669254 ]
 [0.65349806 0.65169456 0.68891242 0.02486069 0.65252976]
 [0.62346383 0.61774225 0.66546728 0.05134274 0.64010507]
 [0.61309287 0.60265238 0.64680797 0.06809668 0.62057243]
 [0.62634123 0.61385204 0.65731883 0.06377309 0.62015425]
 [0.59696672 0.60241673 0.6287547  0.09057195 0.60557924]] -> [0.60420512]
[[0.63737191 0.63961093 0.6678907  0.06302764 0.6669254 ]
 [0.65349806 0.65169456 0.68891242 0.02486069 0.65252976]
 [0.62346383 0.61774225 0.66546728 0.05134274 0.64010507]
 [0.61309287 0.60265238 0.64680797 0.06809668 0.62057243]
 [0.62634123 0.61385204 0.65731883 0.06377309 0.62015425]
 [0.59696672 0.60241673 0.6287547  0.09057195 0.60557924]
 [0.57550507 0.5870322  0.6052186  0.06353081 0.60420512]] -> [0.60498169]
[[0.65349806 0.65169456 0.68891242 0.02486069 0.65252976]
 [0.62346383 0.617742

 [0.71470519 0.7389329  0.7450719  0.11925306 0.75228494]] -> [0.76554563]
[[0.68365194 0.7011494  0.73347024 0.28161166 0.72283633]
 [0.73676653 0.77854405 0.7879033  0.28584208 0.76363411]
 [0.75774849 0.77630412 0.79196218 0.20099145 0.76942846]
 [0.75738882 0.77040963 0.7853586  0.19338788 0.77408749]
 [0.77573302 0.75777195 0.76942555 0.34333476 0.73197538]
 [0.71470519 0.7389329  0.7450719  0.11925306 0.75228494]
 [0.7539117  0.74476875 0.78747919 0.06319536 0.76554563]] -> [0.75443527]
[[0.73676653 0.77854405 0.7879033  0.28584208 0.76363411]
 [0.75774849 0.77630412 0.79196218 0.20099145 0.76942846]
 [0.75738882 0.77040963 0.7853586  0.19338788 0.77408749]
 [0.77573302 0.75777195 0.76942555 0.34333476 0.73197538]
 [0.71470519 0.7389329  0.7450719  0.11925306 0.75228494]
 [0.7539117  0.74476875 0.78747919 0.06319536 0.76554563]
 [0.74839655 0.73313303 0.75009993 0.11604763 0.75443527]] -> [0.73472325]
[[0.75774849 0.77630412 0.79196218 0.20099145 0.76942846]
 [0.75738882 0.770409

ValueError: Variable rnn/basic_lstm_cell/kernel already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 1768, in __init__
    self._traceback = tf_stack.extract_stack()
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 3272, in create_op
    op_def=op_def)
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\util\deprecation.py", line 488, in new_func
    return func(*args, **kwargs)


In [9]:
from __future__ import print_function

import tensorflow as tf
import numpy as np
from tensorflow.contrib import rnn

tf.set_random_seed(777)

sentence = ("if you want to build a ship, don't drum up people together to "
            "collect wood and don't assign them tasks and work, but rather "
            "teach them to long for the endless immensity of the sea.")

char_set = list(set(sentence))
char_dic = {w: i for i, w in enumerate(char_set)}

data_dim = len(char_set)
hidden_size = len(char_set)
num_classes = len(char_set)
sequence_length = 10
learning_rate = 0.1

dataX = []
dataY = []
for i in range(0, len(sentence) - sequence_length):
    x_str = sentence[i:i + sequence_length]
    y_str = sentence[i + 1: i + sequence_length + 1]
    print(i, x_str, '->', y_str)

    x = [char_dic[c] for c in x_str]
    y = [char_dic[c] for c in y_str]

    dataX.append(x)
    dataY.append(y)

batch_size = len(dataX)

X = tf.placeholder(tf.int32, [None, sequence_length])
Y = tf.placeholder(tf.int32, [None, sequence_length])


X_one_hot = tf.one_hot(X, num_classes)
print(X_one_hot)


def lstm_cell():
    cell = rnn.BasicLSTMCell(hidden_size, state_is_tuple=True)
    return cell

multi_cells = rnn.MultiRNNCell([lstm_cell() for _ in range(2)], state_is_tuple=True)


outputs, _states = tf.nn.dynamic_rnn(multi_cells, X_one_hot, dtype=tf.float32)


X_for_fc = tf.reshape(outputs, [-1, hidden_size])
outputs = tf.contrib.layers.fully_connected(X_for_fc, num_classes, activation_fn=None)


outputs = tf.reshape(outputs, [batch_size, sequence_length, num_classes])


weights = tf.ones([batch_size, sequence_length])

sequence_loss = tf.contrib.seq2seq.sequence_loss(
    logits=outputs, targets=Y, weights=weights)
mean_loss = tf.reduce_mean(sequence_loss)
train_op = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(mean_loss)

sess = tf.Session()
sess.run(tf.global_variables_initializer())

for i in range(500):
    _, l, results = sess.run(
        [train_op, mean_loss, outputs], feed_dict={X: dataX, Y: dataY})
    for j, result in enumerate(results):
        index = np.argmax(result, axis=1)
        print(i, j, ''.join([char_set[t] for t in index]), l)

results = sess.run(outputs, feed_dict={X: dataX})
for j, result in enumerate(results):
    index = np.argmax(result, axis=1)
    if j is 0:
        print(''.join([char_set[t] for t in index]), end='')
    else:
        print(char_set[index[-1]], end='')




0 if you wan -> f you want
1 f you want ->  you want 
2  you want  -> you want t
3 you want t -> ou want to
4 ou want to -> u want to 
5 u want to  ->  want to b
6  want to b -> want to bu
7 want to bu -> ant to bui
8 ant to bui -> nt to buil
9 nt to buil -> t to build
10 t to build ->  to build 
11  to build  -> to build a
12 to build a -> o build a 
13 o build a  ->  build a s
14  build a s -> build a sh
15 build a sh -> uild a shi
16 uild a shi -> ild a ship
17 ild a ship -> ld a ship,
18 ld a ship, -> d a ship, 
19 d a ship,  ->  a ship, d
20  a ship, d -> a ship, do
21 a ship, do ->  ship, don
22  ship, don -> ship, don'
23 ship, don' -> hip, don't
24 hip, don't -> ip, don't 
25 ip, don't  -> p, don't d
26 p, don't d -> , don't dr
27 , don't dr ->  don't dru
28  don't dru -> don't drum
29 don't drum -> on't drum 
30 on't drum  -> n't drum u
31 n't drum u -> 't drum up
32 't drum up -> t drum up 
33 t drum up  ->  drum up p
34  drum up p -> drum up pe
35 drum up pe -> rum up peo
36

ValueError: Variable rnn/multi_rnn_cell/cell_0/basic_lstm_cell/kernel already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 1768, in __init__
    self._traceback = tf_stack.extract_stack()
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 3272, in create_op
    op_def=op_def)
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\util\deprecation.py", line 488, in new_func
    return func(*args, **kwargs)


In [10]:
import tensorflow as tf
import numpy as np
import matplotlib
import os

tf.set_random_seed(777)

if "DISPLAY" not in os.environ:

    matplotlib.use('Agg')

import matplotlib.pyplot as plt


def MinMaxScaler(data):

    numerator = data - np.min(data, 0)
    denominator = np.max(data, 0) - np.min(data, 0)

    return numerator / (denominator + 1e-7)



seq_length = 7
data_dim = 5
hidden_dim = 10
output_dim = 1
learning_rate = 0.01
iterations = 500

xy = np.loadtxt('data-02-stock_daily.csv', delimiter=',')
xy = xy[::-1]


train_size = int(len(xy) * 0.7)
train_set = xy[0:train_size]
test_set = xy[train_size - seq_length:]

train_set = MinMaxScaler(train_set)
test_set = MinMaxScaler(test_set)


def build_dataset(time_series, seq_length):
    dataX = []
    dataY = []
    for i in range(0, len(time_series) - seq_length):
        _x = time_series[i:i + seq_length, :]
        _y = time_series[i + seq_length, [-1]]
        print(_x, "->", _y)
        dataX.append(_x)
        dataY.append(_y)
    return np.array(dataX), np.array(dataY)

trainX, trainY = build_dataset(train_set, seq_length)
testX, testY = build_dataset(test_set, seq_length)


X = tf.placeholder(tf.float32, [None, seq_length, data_dim])
Y = tf.placeholder(tf.float32, [None, 1])


cell = tf.contrib.rnn.BasicLSTMCell(
    num_units=hidden_dim, state_is_tuple=True, activation=tf.tanh)
outputs, _states = tf.nn.dynamic_rnn(cell, X, dtype=tf.float32)
Y_pred = tf.contrib.layers.fully_connected(
    outputs[:, -1], output_dim, activation_fn=None)


loss = tf.reduce_sum(tf.square(Y_pred - Y))

optimizer = tf.train.AdamOptimizer(learning_rate)
train = optimizer.minimize(loss)


targets = tf.placeholder(tf.float32, [None, 1])
predictions = tf.placeholder(tf.float32, [None, 1])
rmse = tf.sqrt(tf.reduce_mean(tf.square(targets - predictions)))

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)


    for i in range(iterations):
        _, step_loss = sess.run([train, loss], feed_dict={
                                X: trainX, Y: trainY})
        print("[step: {}] loss: {}".format(i, step_loss))


    test_predict = sess.run(Y_pred, feed_dict={X: testX})
    rmse_val = sess.run(rmse, feed_dict={
                    targets: testY, predictions: test_predict})
    print("RMSE: {}".format(rmse_val))


    plt.plot(testY)
    plt.plot(test_predict)
    plt.xlabel("Time Period")
    plt.ylabel("Stock Price")
    plt.show()

[[2.53065030e-01 2.45070970e-01 2.33983036e-01 4.66075110e-04
  2.32039560e-01]
 [2.29604366e-01 2.39728936e-01 2.54567513e-01 2.98467330e-03
  2.37426028e-01]
 [2.49235510e-01 2.41668371e-01 2.48338489e-01 2.59926504e-04
  2.26793794e-01]
 [2.21013495e-01 2.46602231e-01 2.54710584e-01 0.00000000e+00
  2.62668239e-01]
 [3.63433786e-01 3.70389871e-01 2.67168847e-01 1.24764722e-02
  2.62105010e-01]
 [2.59447633e-01 3.10673724e-01 2.74113889e-01 4.56323384e-01
  2.71751265e-01]
 [2.76008150e-01 2.78314566e-01 1.98470380e-01 5.70171193e-01
  1.78104644e-01]] -> [0.16053716]
[[2.29604366e-01 2.39728936e-01 2.54567513e-01 2.98467330e-03
  2.37426028e-01]
 [2.49235510e-01 2.41668371e-01 2.48338489e-01 2.59926504e-04
  2.26793794e-01]
 [2.21013495e-01 2.46602231e-01 2.54710584e-01 0.00000000e+00
  2.62668239e-01]
 [3.63433786e-01 3.70389871e-01 2.67168847e-01 1.24764722e-02
  2.62105010e-01]
 [2.59447633e-01 3.10673724e-01 2.74113889e-01 4.56323384e-01
  2.71751265e-01]
 [2.76008150e-01 2.7831

 [0.408655   0.43615289 0.44343365 0.17006364 0.45343694]] -> [0.46899786]
[[0.38274503 0.40273941 0.40147738 0.23014251 0.42875817]
 [0.42211043 0.42101143 0.4126143  0.15700457 0.40027695]
 [0.36345895 0.36575282 0.38551098 0.18652864 0.38073802]
 [0.4065505  0.40944246 0.41726462 0.20360312 0.42988455]
 [0.43666969 0.44418322 0.43688238 0.15185086 0.42305471]
 [0.408655   0.43615289 0.44343365 0.17006364 0.45343694]
 [0.43159817 0.44166531 0.46487718 0.12239849 0.46899786]] -> [0.4600908]
[[0.42211043 0.42101143 0.4126143  0.15700457 0.40027695]
 [0.36345895 0.36575282 0.38551098 0.18652864 0.38073802]
 [0.4065505  0.40944246 0.41726462 0.20360312 0.42988455]
 [0.43666969 0.44418322 0.43688238 0.15185086 0.42305471]
 [0.408655   0.43615289 0.44343365 0.17006364 0.45343694]
 [0.43159817 0.44166531 0.46487718 0.12239849 0.46899786]
 [0.45212623 0.44193737 0.47207281 0.15186878 0.4600908 ]] -> [0.50198526]
[[0.36345895 0.36575282 0.38551098 0.18652864 0.38073802]
 [0.4065505  0.4094424

 [0.65223901 0.66931902 0.69194151 0.09448555 0.66722436]] -> [0.75861669]
[[0.63970999 0.69012673 0.68206664 0.1097486  0.70294493]
 [0.69336355 0.70722089 0.71060082 0.14657373 0.68580142]
 [0.67597873 0.68275862 0.71956682 0.06548762 0.70413968]
 [0.66075159 0.64202751 0.66467969 0.14523193 0.65665139]
 [0.66332969 0.65811971 0.68285424 0.04966548 0.6586825 ]
 [0.65223901 0.66931902 0.69194151 0.09448555 0.66722436]
 [0.70049744 0.7622162  0.74080077 0.27411991 0.75861669]] -> [0.7958904]
[[0.69336355 0.70722089 0.71060082 0.14657373 0.68580142]
 [0.67597873 0.68275862 0.71956682 0.06548762 0.70413968]
 [0.66075159 0.64202751 0.66467969 0.14523193 0.65665139]
 [0.66332969 0.65811971 0.68285424 0.04966548 0.6586825 ]
 [0.65223901 0.66931902 0.69194151 0.09448555 0.66722436]
 [0.70049744 0.7622162  0.74080077 0.27411991 0.75861669]
 [0.76278395 0.77984067 0.8163162  0.22005628 0.7958904 ]] -> [0.7688309]
[[0.67597873 0.68275862 0.71956682 0.06548762 0.70413968]
 [0.66075159 0.64202751

ValueError: Variable rnn/basic_lstm_cell/kernel already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 1768, in __init__
    self._traceback = tf_stack.extract_stack()
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\framework\ops.py", line 3272, in create_op
    op_def=op_def)
  File "C:\Users\dwlio\Anaconda3\lib\site-packages\tensorflow\python\util\deprecation.py", line 488, in new_func
    return func(*args, **kwargs)
